In [8]:
from itertools import permutations
import pandas as pd
import pulp as lp


# Defining the data
data = {
    "V1": [6, 4, 5, 7, 2, 5],
    'V2': [2, 9, 2, 6, 3, 5],
    "V3": [6, 9, 2, 6, 9, 2],
    "V4": [7, 5, 1, 7, 5, 2],
    "V5": [4, 3, 9, 3, 7, 8],
    "V6": [2, 8, 4, 9, 2, 1],
    "V7": [5, 5, 3, 2, 6, 4],
    "V8": [9, 8, 3, 7, 5, 3],
    "存货": [60, 55, 51, 43, 41, 52]
}

# Creating the DataFrame
df = pd.DataFrame(data, index=["W1", "W2", "W3", "W4", "W5", "W6"])
df

V1  V2  V3  V4  V5  V6  V7  V8  存货
W1   6   2   6   7   4   2   5   9  60
W2   4   9   9   5   3   8   5   8  55
W3   5   2   2   1   9   4   3   3  51
W4   7   6   6   7   3   9   2   7  43
W5   2   3   9   5   7   2   6   5  41
W6   5   5   2   2   8   1   4   3  52

In [9]:
# Demand
demand = {"V1": 35,"V2":37, "V3": 22, "V4": 32, "V5": 41, "V6": 32, "V7": 43, "V8": 38}

# Adding demand as a row
df = df._append(demand, ignore_index=True)
df.index = ["W1", "W2", "W3", "W4", "W5", "W6", "需求量"]

print(df)
I=list(df.index)
I.pop()
J=list(df.columns)
J.pop()

model = lp.LpProblem('distribution',sense=lp.LpMinimize) # 模型初始化
x = lp.LpVariable.dicts('x',indices=[(i,j) for i in I for j in J],lowBound=0,cat='Integer')
obj = lp.lpSum(df.loc[i,j]*x[i,j] for i in I for j in J)
model += obj # 先添加目标函数
for j in J:
    model += lp.lpSum(x[i,j] for i in I)==df.loc['需求量',j]
for i in I:
    model += lp.lpSum(x[i,j] for j in J)<=df.loc[i,'存货'] 
model.solve()
print(lp.value(model.objective))#result

     V1  V2  V3  V4  V5  V6  V7  V8    存货
W1    6   2   6   7   4   2   5   9  60.0
W2    4   9   9   5   3   8   5   8  55.0
W3    5   2   2   1   9   4   3   3  51.0
W4    7   6   6   7   3   9   2   7  43.0
W5    2   3   9   5   7   2   6   5  41.0
W6    5   5   2   2   8   1   4   3  52.0
需求量  35  37  22  32  41  32  43  38   NaN
596.0


In [10]:
df

V1  V2  V3  V4  V5  V6  V7  V8    存货
W1    6   2   6   7   4   2   5   9  60.0
W2    4   9   9   5   3   8   5   8  55.0
W3    5   2   2   1   9   4   3   3  51.0
W4    7   6   6   7   3   9   2   7  43.0
W5    2   3   9   5   7   2   6   5  41.0
W6    5   5   2   2   8   1   4   3  52.0
需求量  35  37  22  32  41  32  43  38   NaN

In [11]:
df1 = df.copy()
for i in I:
    for j in J:
        df1.loc[i,j] = lp.value(x[i,j])
df1

V1  V2  V3  V4  V5  V6  V7  V8    存货
W1    0  37   0   0   0  21   0   0  60.0
W2    0   0   0   0  41   0   0   0  55.0
W3    0   0   0  32   0   0   0  19  51.0
W4    0   0   0   0   0   0  43   0  43.0
W5   35   0   0   0   0   0   0   0  41.0
W6    0   0  22   0   0  11   0  19  52.0
需求量  35  37  22  32  41  32  43  38   NaN